In [6]:
import re, json, os
from langchain.schema import Document
from sentence_transformers import SentenceTransformer
from langchain.embeddings.base import Embeddings
from langchain_chroma import Chroma
from chromadb import Settings
from google import genai
import requests

In [2]:
path = "./data/alqac25_law.json"

In [7]:
with open(path, "r", encoding="utf8") as f:
    data = json.load(f)


In [8]:
data

[{'id': 'Luật Phòng, chống ma túy',
  'articles': [{'id': '1',
    'text': 'Phạm vi điều chỉnh\n\nLuật này quy định về phòng, chống ma túy; quản lý người sử dụng trái phép chất ma túy; cai nghiện ma túy; trách nhiệm của cá nhân, gia đình, cơ quan, tổ chức trong phòng, chống ma túy; quản lý nhà nước và hợp tác quốc tế về phòng, chống ma túy.'},
   {'id': '2',
    'text': 'Giải thích từ ngữ\n\nTrong Luật này, các từ ngữ dưới đây được hiểu như sau;\n\n1. Chất ma túy là chất gây nghiện, chất hướng thần được quy định trong danh mục chất ma túy do Chính phủ ban hành.\n\n2. Chất gây nghiện là chất kích thích hoặc ức chế thần kinh, dễ gây tình trạng nghiện đối với người sử dụng.\n\n3. Chất hướng thần là chất kích thích hoặc ức chế thần kinh hoặc gây ảo giác, nếu sử dụng nhiều lần có thể dẫn tới tình trạng nghiện đối với người sử dụng.\n\n4. Tiền chất là hóa chất không thể thiếu được trong quá trình điều chế, sản xuất chất ma túy được quy định trong danh mục tiền chất do Chính phủ ban hành.\n\n

In [29]:
df = []

In [30]:
for item in data:
    law_id = item["id"]
    articles = item["articles"]
    for article in articles:
        article_id = article["id"]
        text = article["text"]
        df.append(Document(page_content=text, metadata={"law_id": law_id, "article_id": article_id}))

In [31]:
df

[Document(metadata={'law_id': 'Luật Phòng, chống ma túy', 'article_id': '1'}, page_content='Phạm vi điều chỉnh\n\nLuật này quy định về phòng, chống ma túy; quản lý người sử dụng trái phép chất ma túy; cai nghiện ma túy; trách nhiệm của cá nhân, gia đình, cơ quan, tổ chức trong phòng, chống ma túy; quản lý nhà nước và hợp tác quốc tế về phòng, chống ma túy.'),
 Document(metadata={'law_id': 'Luật Phòng, chống ma túy', 'article_id': '2'}, page_content='Giải thích từ ngữ\n\nTrong Luật này, các từ ngữ dưới đây được hiểu như sau;\n\n1. Chất ma túy là chất gây nghiện, chất hướng thần được quy định trong danh mục chất ma túy do Chính phủ ban hành.\n\n2. Chất gây nghiện là chất kích thích hoặc ức chế thần kinh, dễ gây tình trạng nghiện đối với người sử dụng.\n\n3. Chất hướng thần là chất kích thích hoặc ức chế thần kinh hoặc gây ảo giác, nếu sử dụng nhiều lần có thể dẫn tới tình trạng nghiện đối với người sử dụng.\n\n4. Tiền chất là hóa chất không thể thiếu được trong quá trình điều chế, sản xu

In [32]:
documents_as_dict = [
    {
        "page_content": doc.page_content,
        "metadata": doc.metadata
    }
    for doc in df
]

In [33]:
documents_as_dict

[{'page_content': 'Phạm vi điều chỉnh\n\nLuật này quy định về phòng, chống ma túy; quản lý người sử dụng trái phép chất ma túy; cai nghiện ma túy; trách nhiệm của cá nhân, gia đình, cơ quan, tổ chức trong phòng, chống ma túy; quản lý nhà nước và hợp tác quốc tế về phòng, chống ma túy.',
  'metadata': {'law_id': 'Luật Phòng, chống ma túy', 'article_id': '1'}},
 {'page_content': 'Giải thích từ ngữ\n\nTrong Luật này, các từ ngữ dưới đây được hiểu như sau;\n\n1. Chất ma túy là chất gây nghiện, chất hướng thần được quy định trong danh mục chất ma túy do Chính phủ ban hành.\n\n2. Chất gây nghiện là chất kích thích hoặc ức chế thần kinh, dễ gây tình trạng nghiện đối với người sử dụng.\n\n3. Chất hướng thần là chất kích thích hoặc ức chế thần kinh hoặc gây ảo giác, nếu sử dụng nhiều lần có thể dẫn tới tình trạng nghiện đối với người sử dụng.\n\n4. Tiền chất là hóa chất không thể thiếu được trong quá trình điều chế, sản xuất chất ma túy được quy định trong danh mục tiền chất do Chính phủ ban hà

## Embeddings

In [34]:
import torch

In [ ]:
embedding_model_name = "BAAI/bge-m3"
device = 'cuda' if torch.cuda.is_available() else 'cpu'
embedding_model = SentenceTransformer(embedding_model_name, device=device)


In [38]:
with open("law_articles.jsonl", "w", encoding="utf-8") as f:
    for doc in documents_as_dict:
        f.write(json.dumps(doc, ensure_ascii=False) + "\n")

## Weaviate

In [39]:
import json
with open('documents.json', 'r', encoding='utf-8') as f:
    documents = json.load(f)

In [49]:
documents[0]

{'page_content': 'Phạm vi điều chỉnh\n\nLuật này quy định về phòng, chống ma túy; quản lý người sử dụng trái phép chất ma túy; cai nghiện ma túy; trách nhiệm của cá nhân, gia đình, cơ quan, tổ chức trong phòng, chống ma túy; quản lý nhà nước và hợp tác quốc tế về phòng, chống ma túy.',
 'metadata': {'law_id': 'Luật Phòng, chống ma túy', 'article_id': '1'},
 'embedding': [0.010806294158101082,
  0.023161210119724274,
  -0.008988224901258945,
  -0.016378823667764664,
  -0.009372679516673088,
  -0.05664585903286934,
  0.01915539801120758,
  0.014986163936555386,
  0.015514484606683254,
  0.004754009190946817,
  -0.07181164622306824,
  -0.023586414754390717,
  -0.03985236585140228,
  -0.037192221730947495,
  -0.0040182871744036674,
  -0.004994185175746679,
  0.011576564982533455,
  -0.019833842292428017,
  -0.044059548527002335,
  -0.05110781267285347,
  -0.04465673491358757,
  0.0013354099355638027,
  -0.011915345676243305,
  0.019139489158988,
  -0.0044416100718081,
  -0.0104450853541493

In [5]:
import weaviate
import weaviate.classes as wvc
from weaviate.classes.config import (
    Configure,
    Property,
    DataType,
    VectorDistances, 
)
from sentence_transformers import SentenceTransformer
from langchain.embeddings.base import Embeddings

c:\Python310\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
c:\Python310\lib\site-packages\tensorflow\python\framework\dtypes.py:35: DeprecationWarning: ml_dtypes.float8_e4m3b11 is deprecated. Use ml_dtypes.float8_e4m3b11fnuz
  from tensorflow.tsl.python.lib.core import pywrap_ml_dtypes


In [6]:
# ==== Embedding Model ====
class CustomSentenceTransformerEmbeddings(Embeddings):
    def __init__(self, model_id='BAAI/bge-m3'):
        self.model = SentenceTransformer(model_id, trust_remote_code=True)

    def embed_documents(self, texts):
        return self.model.encode(texts, convert_to_tensor=False).tolist()

    def embed_query(self, text):
        return self.model.encode([text], convert_to_tensor=False)[0].tolist()

embedding_model = CustomSentenceTransformerEmbeddings()

In [43]:
client = weaviate.connect_to_local()

In [48]:
names = "alqac"

In [50]:
client.collections.delete(names) 
# # # Tạo schema mới có hỗ trợ hybrid (BM25 + vector)

client.collections.create(
    name=names,
    description="ALQAC",
    inverted_index_config=Configure.inverted_index(bm25_b=0.75, bm25_k1=1.2),
    vectorizer_config=Configure.Vectorizer.none(),
    vector_index_config=Configure.VectorIndex.flat(distance_metric=VectorDistances.COSINE),
    properties=[
        Property(name="page_content", data_type=DataType.TEXT),
        Property(name="law_id", data_type=DataType.TEXT),
        Property(name="article_id", data_type=DataType.TEXT),
    ]
)

print(f"✅ Created schema {names} successfully.")
client.close()

c:\Python310\lib\site-packages\weaviate\collections\classes\config.py:1950: PydanticDeprecatedSince211: Accessing the 'model_fields' attribute on the instance is deprecated. Instead, you should access this attribute from the model class. Deprecated in Pydantic V2.11 to be removed in V3.0.
  for cls_field in self.model_fields:


✅ Created schema alqac successfully.


In [51]:
client = weaviate.connect_to_local()
collection = client.collections.get(names)

In [52]:
total = len(documents)
success_count = 0
fail_count = 0
with collection.batch.dynamic() as batch:
            for obj in documents:
                try:
                    metadata = {
                        "page_content": obj["page_content"],
                        "law_id": obj["metadata"]["law_id"],
                        "article_id": obj["metadata"]["article_id"],
                    }


                    batch.add_object(
                        properties=metadata,
                        vector=obj["embedding"]
                    )
                    success_count += 1

                except Exception as e:
                    print(f"Lỗi khi thêm object {obj['page_content']}: {e}")
                    fail_count += 1
print(f"Tổng vector trong file: {total}")
print(f"Thành công: {success_count}")
print(f"Thất bại: {fail_count}")
print(f"Tổng đã xử lý: {success_count + fail_count}")
client.close()

Tổng vector trong file: 3368
Thành công: 3368
Thất bại: 0
Tổng đã xử lý: 3368


In [53]:
client = weaviate.connect_to_local()
collection = client.collections.get("alqac")
count = client.collections.get("alqac").aggregate.over_all()
print(f"Số vector: {count}")
client.close()

Số vector: AggregateReturn(properties={}, total_count=3368)


## RAG

In [1]:
import weaviate
from typing import List

client = weaviate.connect_to_local()
collection = client.collections.get("alqac")

In [2]:
query = 'Người nghiện ma túy từ đủ 18 tuổi trở lên bị áp dụng biện pháp xử lý hành chính đưa vào cơ sở cai nghiện bắt buộc theo quy định của Luật Xử lý vi phạm hành chính khi bị phát hiện sử dụng chất ma túy một cách trái phép trong thời gian cai nghiện ma túy tự nguyện, đúng hay sai?'

In [7]:
res1 = collection.query.hybrid(
    query=query,
    vector=embedding_model.embed_query(query),
    limit=5,
    alpha=0.2,
    return_metadata=["score"],
)

In [ ]:
for obj in res1.objects:
    print("Score:", obj.metadata.score)
    print("Law ID:", obj.properties.get("law_id"))
    print("Article ID:", obj.properties.get("article_id"))
    print("Nội dung:", obj.properties["page_content"])
    print("---")

Score: 1.0
Chương: None
Mục: None
Điều: None
Khoản: None
Nội dung: Đối tượng bị áp dụng biện pháp xử lý hành chính đưa vào cơ sở cai nghiện bắt buộc

Người nghiện ma túy từ đủ 18 tuổi trở lên bị áp dụng biện pháp xử lý hành chính đưa vào cơ sở cai nghiện bắt buộc theo quy định của Luật Xử lý vi phạm hành chính khi thuộc một trong các trường hợp sau đây:

1. Không đăng ký, không thực hiện hoặc tự ý chấm dứt cai nghiện ma túy tự nguyện;

2. Trong thời gian cai nghiện ma túy tự nguyện bị phát hiện sử dụng trái phép chất ma túy;

3. Người nghiện ma túy các chất dạng thuốc phiện không đăng ký, không thực hiện hoặc tự ý chấm dứt điều trị nghiện các chất dạng thuốc phiện bằng thuốc thay thế hoặc bị chấm dứt điều trị nghiện các chất dạng thuốc phiện bằng thuốc thay thế do vi phạm quy định về điều trị nghiện;

4. Trong thời gian quản lý sau cai nghiện ma túy mà tái nghiện.
---
Score: 0.9254600405693054
Chương: None
Mục: None
Điều: None
Khoản: None
Nội dung: Cai nghiện ma túy cho người từ đủ 12 